In [78]:
from datasets import load_dataset
from datasets import concatenate_datasets
from IPython.display import HTML

from tqdm import tqdm
import re 
import numpy as np
from markdownify import markdownify as md

In [2]:
ds = load_dataset("HuggingFaceH4/stack-exchange-preferences", split="train", num_proc=16)
ds

Found cached dataset parquet (/home/leandro/.cache/huggingface/datasets/HuggingFaceH4___parquet/HuggingFaceH4--stack-exchange-preferences-1d2bff9ecb5ffe2a/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec)


In [6]:
HTML(ds[0]["question"])

In [7]:
def lang_callback(el):
    lang = el['class'][0] if el.has_attr('class') else None
    
    if not lang is None:
        lang = lang.split("-")[-1]
    return lang

In [57]:
def html2md(text):
    text = md(text, code_language_callback=lang_callback)
    text = re.sub(r"\n\s*\n", "\n\n", text).strip()
    return text.encode('utf-8', 'replace').decode()

In [77]:
for i in range(1):
    text = html2md(ds[i]["question"])
    print(text)
    print("=="*10)

I have been wanting to learn about 3D printing a long time so I really want this site to succeed but I have no previous experience with the subject. 

I was wondering how can I help the site at this early stage. I thought about asking about how to get started with 3D printing but SE explicitly discourages "easy" questions in the private beta.

What can newbies like me do for the site at this stage besides voting questions and answers?


In [13]:
np.mean([len(ds[i]["answers"])*(len(ds[i]["answers"])-1)/2 for i in range(10000)])

49.935

In [58]:
def binary_comparison(answers):
    """Returns tuples of answers, first always best"""
    pairs = []
    
    for i in range(len(answers)-1):
        for j in range(i+1, len(answers)):
            if answers[i]["pm_score"]>answers[j]["pm_score"]:
                pairs.append((answers[i]["text"], answers[j]["text"]))
            elif answers[i]["pm_score"]<answers[j]["pm_score"]:
                pairs.append((answers[j]["text"], answers[i]["text"]))
    return pairs

In [63]:
def preprocess(examples):
    """Cleans HTML and returns paired answers (j is better than k). Note that this returns more examples (one for each pair per question)."""
    
    MAX_PAIRS_PER_QUESTION = 10
    n_samples = len(examples["qid"])
    
    # initialize empty lists for new samples
    new_examples = {"question": [], "response_j": [], "response_k": []}
    for key in examples:
        new_examples[key] = []
    
    for sample_id in range(n_samples):
        # get pairs where first is always the better one
        pairs = binary_comparison(examples["answers"][sample_id])
        n_answers = len(examples["answers"][sample_id])
        
        # sample if we get more pairs than maximum
        if len(pairs) > MAX_PAIRS_PER_QUESTION:
            indices = np.random.choice(list(range(len(pairs))), MAX_PAIRS_PER_QUESTION, replace=False)
            pairs = [pairs[i] for i in indices]
        
        # construct the samples
        for pair in pairs:
            for key in examples:
                if key=="question":
                    new_examples[key].append(html2md(examples[key][sample_id]))
                else:
                    new_examples[key].append(examples[key][sample_id])
            new_examples["response_j"].append(html2md(pair[0]))
            new_examples["response_k"].append(html2md(pair[1]))
    return new_examples

In [64]:
ds_result = ds.map(preprocess, batch_size=1000, batched=True, num_proc=60)

Map (num_proc=60):   0%|          | 0/10807695 [00:00<?, ? examples/s]

/opt/conda/envs/jupyter/lib/python3.8/site-packages/bs4/__init__.py:435: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  warnings.warn(
/opt/conda/envs/jupyter/lib/python3.8/site-packages/bs4/__init__.py:435: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  warnings.warn(
/opt/conda/envs/jupyter/lib/python3.8/site-packages/bs4/__init__.py:435: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  warnings.warn(
/opt/conda/envs/jupyter/lib/python3.8/site-packages/bs4/__init__.py:435: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  warnings.warn(


In [65]:
ds_result

Dataset({
    features: ['qid', 'question', 'answers', 'date', 'metadata', 'response_j', 'response_k'],
    num_rows: 26801833
})

In [47]:
ds_result[0]

{'qid': 1,
 'question': 'I have been wanting to learn about 3D printing a long time so I really want this site to succeed but I have no previous experience with the subject. \n\nI was wondering how can I help the site at this early stage. I thought about asking about how to get started with 3D printing but SE explicitly discourages "easy" questions in the private beta.\n\nWhat can newbies like me do for the site at this stage besides voting questions and answers?',
 'answers': [{'answer_id': 14,
   'author': 'Eric Johnson',
   'author_id': 43,
   'author_profile': 'https://3dprinting.meta.stackexchange.com/users/43',
   'pm_score': 2,
   'selected': False,
   'text': '<p>I would suggest doing a bit of basic research on 3D printing (including reading questions and answers).  From these you will learn more about it and hopefull you will have new questions about 3D printing that can be asked.  </p>\n\n<p>If you are looking at getting a 3D printer, you could ask about different features li

In [67]:
ds_result = ds_result.remove_columns(["answers"])

In [71]:
ds_result[199]

{'qid': 5,
 'question': 'What are the main differences when using ABS over PLA and vice versa?',
 'date': '2016/01/12',
 'metadata': ['https://3dprinting.stackexchange.com/questions/5',
  'https://3dprinting.stackexchange.com',
  'https://3dprinting.stackexchange.com/users/11/'],
 'response_j': "Paraphrasing [this](http://www.protoparadigm.com/news-updates/the-difference-between-abs-and-pla-for-3d-printing/) site. Feel free to add suggestions in the form of comments and I will try to incorporate them.\n\nSummary\n\n* ABS: Stronger, machinable, more flexible, and more temperature\nresistant than PLA. Typically printed on a heated bed. Warping is a common problem when printing ABS.\n* PLA: Wider range of filaments available, easier and in some cases faster to print. Not as strong as ABS and the fact that its biodegradable could be seen as both a benefit and a drawback.\n\nMaterial Properties:\n\n* ABS: Strong plastic with mild flexibility. Naturally beige in color. Can be filled and sand

In [72]:
ds_result = ds_result.shuffle(seed=42)

In [73]:
ds_result

Dataset({
    features: ['qid', 'question', 'date', 'metadata', 'response_j', 'response_k'],
    num_rows: 26801833
})

In [74]:
ds_result[0]

{'qid': 48865595,
 'question': 'I am using [AGM maps](https://angular-maps.com/) for my angular 4 application, there I am facing issues, I will be having the multiple markers which are fetched from api as an array of Latitude and Longitude. I want to set the zoom level exactly covering all the markers on the map. Even if one marker in one country and other in some other country also, It should set the zoom level on load to show all the markers on the map.\n Is there a way to do that in AGM angular maps? Could anyone please help me',
 'date': '2018/02/19',
 'metadata': ['https://Stackoverflow.com/questions/48865595',
  'https://Stackoverflow.com',
  'https://Stackoverflow.com/users/4715138/'],
 'response_j': 'Since September 2018 there is the [`AgmFitBounds`](https://angular-maps.com/api-docs/agm-core/directives/agmfitbounds) directive. Super easy.\n\n```\n<agm-map\n  style="width:100vw; height:100vh;"\n  [fitBounds]="true">\n\n  <agm-marker\n    *ngFor="let location of locations"\n    

In [75]:
import os
import time
from multiprocessing import Pool
from tqdm import tqdm

from huggingface_hub import Repository


def save_shard(shard_tuple):
    """Save shard"""
    filename, shard = shard_tuple
    # use to_json instead to save as json file
    shard.to_parquet(filename)


def save_manual_shards(ds, user="lvwerra", remote_dataset_repo="stack-exchange-paired"):
    """Save sharded data
    Args:
        ds (Dataset): dataset to be saved
        user (str): user name
        remote_dataset_repo (str): remote dataset repository
        out_path (str): path to save the shards"""
    # this will create a folder OUT_PATH that is a clone of REMOTE_DATASET_REPO
    # you can save the shards inside it and do git add/commit/push to push data to the hub
    out_path = remote_dataset_repo
    # if out path doesnt already exist
    if not os.path.exists(out_path):
        repo = Repository(
            local_dir=out_path,
            clone_from=user + "/" + remote_dataset_repo,
            repo_type="dataset",
            private=False,
            use_auth_token=True,
            git_user=user,
        )

    # files will be numerous we save them in a folder called data inside out_path
    os.mkdir(out_path + "/data")
    SHARD_SIZE = 1000 << 20
    if ds._indices is not None:
        dataset_nbytes = ds.data.nbytes * len(ds._indices) / len(ds.data)
    else:
        dataset_nbytes = ds.data.nbytes
    num_shards = int(dataset_nbytes / SHARD_SIZE) + 1
    print(f"Number of shards: {num_shards}")

    print("sharding the dataset")
    t_start = time.time()
    shards = (
        ds.shard(num_shards=num_shards, index=i, contiguous=True)
        for i in range(num_shards)
    )
    # use f"{OUT_PATH}/data/train-{index:05d}-of-{num_shards:05d}.json" instead for json files
    filenames = (
        f"{out_path}/data/train-{index:05d}-of-{num_shards:05d}.parquet"
        for index in range(num_shards)
    )

    with Pool(16) as p:
        list(
            tqdm(
                p.imap_unordered(save_shard, zip(filenames, shards), chunksize=4),
                total=num_shards,
            )
        )
    print(f"Time to save dataset: {time.time()-t_start:.2f}")
    # to push dataset to hub do: git add/commit/push inside OUT_PATH

In [76]:
save_manual_shards(ds_result)

Cloning https://huggingface.co/datasets/lvwerra/stack-exchange-paired into local empty directory.


Number of shards: 72
sharding the dataset


100%|███████████████████████████████████████████████████████████████| 72/72 [03:50<00:00,  3.20s/it]


Time to save dataset: 231.51
